In [3]:
#Importing the required libraries
import pandas as pd
from sklearn.model_selection import train_test_split 
import time
import numpy as np
from sklearn.preprocessing import StandardScaler
from sklearn.feature_selection import SelectKBest
from sklearn.feature_selection import chi2
from sklearn.feature_selection import RFE
from sklearn.linear_model import LogisticRegression
import pickle
import matplotlib.pyplot as plt

# Creating a functions 1) to select the k value(no of features), 2)standard scalar to split the train and test set
# 3) confusion matrix and classification report to check the accuracy
# 4) creating the models for various classification algorithms
# 5) preparing a table of various calssification algorithms and the accuracy value
def selectkbest(indep_X,dep_Y,n):
        test = SelectKBest(score_func=chi2, k=n)
        fit1= test.fit(indep_X,dep_Y)
        selectk_features = fit1.transform(indep_X)
        return selectk_features
def split_scalar(indep_X,dep_Y):
        X_train, X_test, y_train, y_test = train_test_split(indep_X, dep_Y, test_size = 0.25, random_state = 0)
        sc = StandardScaler()
        X_train = sc.fit_transform(X_train)
        X_test = sc.transform(X_test)    
        return X_train, X_test, y_train, y_test

    
def cm_prediction(grid,X_test):
         y_pred = grid.predict(X_test)
         from sklearn.metrics import confusion_matrix
         cm = confusion_matrix(y_test, y_pred)
         from sklearn.metrics import classification_report
         from sklearn.metrics import roc_auc_score
         Accuracy=roc_auc_score(y_test,grid.predict_proba(X_test)[:,1])
         report=classification_report(y_test, y_pred)
         return  grid,Accuracy,report,X_test,y_test,cm
        
def logistic(X_train,y_train,X_test):       
        # Fitting Logistic regression to the Training set
        from sklearn.linear_model import LogisticRegression
        from sklearn.model_selection import GridSearchCV
        param_grid={'solver':['lbfgs', 'liblinear', 'newton-cg', 'saga'],'penalty':['l2']}
        grid=GridSearchCV(LogisticRegression(),param_grid,refit=True,verbose=3,n_jobs=-1, scoring='f1_weighted')
        grid.fit(X_train, y_train)
        grid,Accuracy,report,X_test,y_test,cm=cm_prediction(grid,X_test)
        return  grid,Accuracy,report,X_test,y_test,cm  

def svm(X_train,y_train,X_test):
                
        from sklearn.svm import SVC
        from sklearn.model_selection import GridSearchCV
        param_grid={'kernel':['linear', 'poly', 'rbf','sigmoid'],'C':[10,100,500,700,1000,2000,3000],'gamma':['auto', 'scale']}
        grid=GridSearchCV(SVC(probability=True),param_grid,refit=True,verbose=3,cv=5,n_jobs=-1,scoring='f1_weighted')
        grid.fit(X_train,y_train)
        grid,Accuracy,report,X_test,y_test,cm=cm_prediction(grid,X_test)
        return  grid,Accuracy,report,X_test,y_test,cm
def Decision(X_train,y_train,X_test):
                
        from sklearn.svm import SVC
        from sklearn.model_selection import GridSearchCV
        param_grid={'kernel':['linear', 'poly', 'rbf','sigmoid'],'C':[10,100,500,700,1000,2000,3000],'gamma':['auto', 'scale']}
        grid=GridSearchCV(SVC(probability=True),param_grid,refit=True,verbose=3,cv=5,n_jobs=-1,scoring='f1_weighted')
        grid.fit(X_train,y_train)
        grid,Accuracy,report,X_test,y_test,cm=cm_prediction(grid,X_test)
        return  grid,Accuracy,report,X_test,y_test,cm
def random(X_train,y_train,X_test):
        
        # Fitting RF to the Training set
        from sklearn.ensemble import RandomForestClassifier
        from sklearn.model_selection import GridSearchCV
        param_grid={'criterion':['gini','entropy','log_loss'],'max_features':['sqrt','log2'],'n_estimators':[10,100]}
        grid=GridSearchCV(RandomForestClassifier(),param_grid,verbose=3,refit=True,n_jobs=-1,scoring='f1_weighted')
        grid.fit(X_train,y_train)
        grid,Accuracy,report,X_test,y_test,cm=cm_prediction(grid,X_test)
        return  grid,Accuracy,report,X_test,y_test,cm
def selectk_Classification(acclog,accsvm,accdes,accrf): 
    
    dataframe=pd.DataFrame(index=['ChiSquare'],columns=['Logistic','SVM','Decision','Random'])
    for number,idex in enumerate(dataframe.index):      
        dataframe['Logistic'][idex]=acclog[number]       
        dataframe['SVM'][idex]=accsvm[number]
        dataframe['Decision'][idex]=accdes[number]
        dataframe['Random'][idex]=accrf[number]
    return dataframe   

In [4]:
dataset=pd.read_csv('Emp_Attrition.csv')
#setting display options to display the columns and rows in a dataset
pd.set_option('display.max_columns',None)
pd.set_option('display.max_rows',None)
#setting the display option of maximum width without truncating the data
pd.set_option('display.width',None)
#reads the dataset and displays the rows and columns without truncating the data in the dataset
dataset

Age Attrition     BusinessTravel  DailyRate              Department  \
0      41       Yes      Travel_Rarely       1102                   Sales   
1      49        No  Travel_Frequently        279  Research & Development   
2      37       Yes      Travel_Rarely       1373  Research & Development   
3      33        No  Travel_Frequently       1392  Research & Development   
4      27        No      Travel_Rarely        591  Research & Development   
5      32        No  Travel_Frequently       1005  Research & Development   
6      59        No      Travel_Rarely       1324  Research & Development   
7      30        No      Travel_Rarely       1358  Research & Development   
8      38        No  Travel_Frequently        216  Research & Development   
9      36        No      Travel_Rarely       1299  Research & Development   
10     35        No      Travel_Rarely        809  Research & Development   
11     29        No      Travel_Rarely        153  Research & Development   
12     31        No      Travel_Rarely        670  Research & Development   
13     34        No      Travel_Rarely       1346  Research & Development   
14     28       Yes      Travel_Rarely        103  Research & Development   
15     29        No      Travel_Rarely       1389  Research & Development   
16     32        No      Travel_Rarely        334  Research & Development   
17     22        No         Non-Travel       1123  Research & Development   
18     53        No      Travel_Rarely       1219                   Sales   
19     38        No      Travel_Rarely        371  Research & Development   
20     24        No         Non-Travel        673  Research & Development   
21     36       Yes      Travel_Rarely       1218                   Sales   
22     34        No      Travel_Rarely        419  Research & Development   
23     21        No      Travel_Rarely        391  Research & Development   
24     34       Yes      Travel_Rarely        699  Research & Development   
25     53        No      Travel_Rarely       1282  Research & Development   
26     32       Yes  Travel_Frequently       1125  Research & Development   
27     42        No      Travel_Rarely        691                   Sales   
28     44        No      Travel_Rarely        477  Research & Development   
29     46        No      Travel_Rarely        705                   Sales   
30     33        No      Travel_Rarely        924  Research & Development   
31     44        No      Travel_Rarely       1459  Research & Development   
32     30        No      Travel_Rarely        125  Research & Development   
33     39       Yes      Travel_Rarely        895                   Sales   
34     24       Yes      Travel_Rarely        813  Research & Development   
35     43        No      Travel_Rarely       1273  Research & Development   
36     50       Yes      Travel_Rarely        869                   Sales   
37     35        No      Travel_Rarely        890                   Sales   
38     36        No      Travel_Rarely        852  Research & Development   
39     33        No  Travel_Frequently       1141                   Sales   
40     35        No      Travel_Rarely        464  Research & Development   
41     27        No      Travel_Rarely       1240  Research & Development   
42     26       Yes      Travel_Rarely       1357  Research & Development   
43     27        No  Travel_Frequently        994                   Sales   
44     30        No  Travel_Frequently        721  Research & Development   
45     41       Yes      Travel_Rarely       1360  Research & Development   
46     34        No         Non-Travel       1065                   Sales   
47     37        No      Travel_Rarely        408  Research & Development   
48     46        No  Travel_Frequently       1211                   Sales   
49     35        No      Travel_Rarely       1229  Research & Development   
50     48       Yes      Travel_Rarely        626  Research & Development   
51

In [5]:
# converting the categorical values in to numerical values using get dummies
dataset=pd.get_dummies(dataset,drop_first=True)
dataset

Age  DailyRate  DistanceFromHome  Education  EmployeeCount  \
0      41       1102                 1          2              1   
1      49        279                 8          1              1   
2      37       1373                 2          2              1   
3      33       1392                 3          4              1   
4      27        591                 2          1              1   
5      32       1005                 2          2              1   
6      59       1324                 3          3              1   
7      30       1358                24          1              1   
8      38        216                23          3              1   
9      36       1299                27          3              1   
10     35        809                16          3              1   
11     29        153                15          2              1   
12     31        670                26          1              1   
13     34       1346                19          2              1   
14     28        103                24          3              1   
15     29       1389                21          4              1   
16     32        334                 5          2              1   
17     22       1123                16          2              1   
18     53       1219                 2          4              1   
19     38        371                 2          3              1   
20     24        673                11          2              1   
21     36       1218                 9          4              1   
22     34        419                 7          4              1   
23     21        391                15          2              1   
24     34        699                 6          1              1   
25     53       1282                 5          3              1   
26     32       1125                16          1              1   
27     42        691                 8          4              1   
28     44        477                 7          4              1   
29     46        705                 2          4              1   
30     33        924                 2          3              1   
31     44       1459                10          4              1   
32     30        125                 9          2              1   
33     39        895                 5          3              1   
34     24        813                 1          3              1   
35     43       1273                 2          2              1   
36     50        869                 3          2              1   
37     35        890                 2          3              1   
38     36        852                 5          4              1   
39     33       1141                 1          3              1   
40     35        464                 4          2              1   
41     27       1240                 2          4              1   
42     26       1357                25          3              1   
43     27        994                 8          3              1   
44     30        721                 1          2              1   
45     41       1360                12          3              1   
46     34       1065                23          4              1   
47     37        408                19          2              1   
48     46       1211                 5          4              1   
49     35       1229                 8          1              1   
50     48        626                 1          2              1   
51     28       1434                 5          4              1   
52     44       1488                 1          5              1   
53     35       1097                11          2              1   
54     26       1443                23          3              1   
55     33        515                 1          2              1   
56     35        853                18          5              1   
57     35       1142                23          4             

In [6]:
dataset.shape

(1470, 48)

In [7]:
# storing the dataset in a different dataframe df2 and working using that
# selecting the k value( no of features ) here to calculate the chi square value 
dataset1=pd.read_csv("Emp_attrition.csv",index_col=None)

df2=dataset1

df2 = pd.get_dummies(df2, drop_first=True)

indep_X=df2.drop('Attrition_Yes', 1)
dep_Y=df2['Attrition_Yes']


kbest=selectkbest(indep_X,dep_Y,4)       

acclog=[]
accsvm=[]
accdes=[]
accrf=[]

C:\Users\Lenovo\AppData\Local\Temp\ipykernel_4556\4235020156.py:9: FutureWarning: In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only.
  indep_X=df2.drop('Attrition_Yes', 1)


In [8]:
X_train, X_test, y_train, y_test=split_scalar(kbest,dep_Y)   
    

In [ ]:
# checking the classification report, accuracy, confusion matrix for all the vlassification models such as logistic, svm ,
#decision tree and RF 
grid,Accuracy,report,X_test,y_test,cm=logistic(X_train,y_train,X_test)
acclog.append(Accuracy)

grid,Accuracy,report,X_test,y_test,cm=svm_linear(X_train,y_train,X_test)  
accsvm.append(Accuracy)
    

grid,Accuracy,report,X_test,y_test,cm=Decision(X_train,y_train,X_test)  
accdes.append(Accuracy)
    
grid,Accuracy,report,X_test,y_test,cm=random(X_train,y_train,X_test)  
accrf.append(Accuracy)

Fitting 5 folds for each of 4 candidates, totalling 20 fits


In [2]:
result=selectk_Classification(acclog,accsvm,accdes,accrf)

NameError: name 'selectk_Classification' is not defined

In [ ]:
# Checking the performance of the various models with 5 independent features
result
#5

In [ ]:
result
#6

In [ ]:
result
#4

In [ ]:
# based on the above result 84% keeps repeating ( mode) ..hence the accuracy of this problem is 84%  with k value as 4 ...
# which means instead of working with 48 columns, with 4 necessary features , the models produce an accuracy of 84%